Introducing further constraints to the randomness will result in designs that give the impression of conforming to an underlying system (and, let's hypothesize, thereby give an impression of being more like "writing").

The strokes produced by the flat library have a uniform width and texture, which makes the resulting artifacts resemble drawings made with a very precise pen. The problem of how to simulate how different writing implements make marks on a page ("brushes" in a tool like PhotoShop) is an open area of research in computer graphics research. (A recent review.)

Working with a limited set of glyphs (in my experience) provides a bit of verisimilitude, since you expect to see repeated figures in handwriting. But you also have to be careful to add a bit of variation to the glyphs, because otherwise it can look a bit "robotic." (Though "robotic" might be exactly what you're going for. I don't know.)

In [1]:
from flat import document, shape, rgba

In [2]:
from IPython.display import SVG, display
def show(page):
    display(SVG(page.svg()))

In [3]:
from bezmerizing import Polyline

In [4]:
import numpy as np

In [396]:
from numpy.random import uniform, normal, choice, randint

In [10]:
from scipy.stats import truncnorm
def t_normal(a, b, mu, sigma):
    tn = truncnorm((a-mu)/sigma, (b-mu)/sigma, loc=mu, scale=sigma)
    return tn.rvs(1)[0]

In [6]:
def make_char():
    pts = []
    for i in range(int(t_normal(4, 12, 8, 2))):
        x = (choice([0, 0.5, 1, 1.5]))
        y = (choice([0, 0.5, 1, 1.5]))
        pts.append([x, y])
    return Polyline(pts)

In [7]:
def make_scribble(width, height, steps, stddev=0):
    pts = []
    for i in range(steps):
        x = ((width / steps) * i) + normal(0, stddev)
        y = normal(0, height)
        pts.append([x, y])
    return Polyline(pts)

In [105]:
thicknesses = (np.sin(np.linspace(0, np.pi*4, 100))+1) * 12

In [110]:
poly = Polyline(pts).augment().fancy_curve(thicknesses=thicknesses, samples_per=54)

In [111]:
d = document(600, 600, 'pt')
page = d.addpage()
curve_fig = shape().fill(rgba(40, 40, 40, 255)).nostroke()
page.place(curve_fig.polygon(poly))

point_fig = shape().stroke(rgba(0, 0, 0, 255)).fill(rgba(255, 255, 255, 255)).width(1)
for pt in Polyline(pts).vertices:
    page.place(point_fig.circle(*pt, 2))
show(page)

control thickness for a single stroke (down-stroke, move, up-stroke)


In [296]:
pts = [[np.random.normal(300, 100), np.random.normal(300, 100)] for i in range(6)]

In [297]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 12

In [298]:
poly = Polyline(pts).augment().fancy_curve(thicknesses=thicknesses, samples_per=54)

In [299]:
d = document(400, 400, 'pt')
page = d.addpage()
curve_fig = shape().fill(rgba(40, 40, 40, 255)).nostroke()
page.place(curve_fig.polygon(poly))

point_fig = shape().stroke(rgba(0, 0, 0, 255)).fill(rgba(255, 255, 255, 255)).width(1)
for pt in Polyline(pts).vertices:
    page.place(point_fig.circle(*pt, 2))
show(page)

Define a make radical function

In [338]:
def make_radical(x_norms, y_norms, num_pts_norms):
    pts = []
    for i in range(int(t_normal(*num_pts_norms))):
        x = t_normal(*x_norms)
        y = t_normal(*y_norms)
        pts.append([x, y])
    return Polyline(pts)    

Start to make radicles on the left, right, top, bottom:

In [272]:
left_radicals = [make_radical((0, 1, 0.25, 0.1), (0, 1, 0.5, 0.5), (2, 8, 4, 2)) for i in range(10)]
right_radicals = [make_radical((0, 1, 0.75, 0.1), (0, 1, 0.5, 0.5), (2, 8, 4, 2)) for i in range(10)]
top_radicals = [make_radical((0, 1, 0.5, 0.5), (0, 1, 0.25, 0.1), (2, 8, 4, 2)) for i in range(10)]
bottom_radicals = [make_radical((0, 1, 0.5, 0.5), (0, 1, 0.75, 0.1), (2, 8, 4, 2)) for i in range(10)]

In [312]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
# poly = Polyline(scaled_pts).augment().fancy_curve(thicknesses=thicknesses, samples_per=54)

In [315]:
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        radical_pline = choice(left_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
        radical_pline = choice(right_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
        radical_pline = choice(top_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
        radical_pline = choice(bottom_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
show(page)

The result is interesting, but they aren't quite look like characters, since:
1. They somewhat overlaps too much
2. The rapitition rate is a little too high
3. Missing stand-alone radicals
4. Radicals are made of only one polyline
5. The composition of each character are the same.

Now try to control the bounding box of each type of radicals:

In [318]:
left_radicals = [make_radical((0, 0.7, 0.2, 0.1), (0, 1, 0.5, 0.5), (2, 8, 4, 2)) for i in range(10)]
right_radicals = [make_radical((0.3, 1, 0.8, 0.1), (0, 1, 0.5, 0.5), (2, 8, 4, 2)) for i in range(10)]
top_radicals = [make_radical((0, 1, 0.5, 0.5), (0, 0.7, 0.2, 0.1), (2, 8, 4, 2)) for i in range(10)]
bottom_radicals = [make_radical((0, 1, 0.5, 0.5), (0.3, 1, 0.8, 0.1), (2, 8, 4, 2)) for i in range(10)]

In [319]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        radical_pline = choice(left_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
        radical_pline = choice(right_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
        radical_pline = choice(top_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
        radical_pline = choice(bottom_radicals).scale(grid_size * 0.67).translate(3 + i * grid_size, 3 + j * grid_size)
        poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses)
        poly = figure.polygon(poly)
        page.place(poly)
show(page)

Then try to create stand-alone radicals with multiple strokes:


In [339]:
def make_radical_multi(x_norms, y_norms, num_pts_norms, num_strokes):
    p_lines = []
    for i in range(num_strokes):
        pts = []
        for i in range(int(t_normal(*num_pts_norms))):
            x = t_normal(*x_norms)
            y = t_normal(*y_norms)
            pts.append([x, y])
        p_lines.append(Polyline(pts))
    
    return p_lines

In [735]:
def scale_shift_radical_multi(p_lines, scale, x_off, y_off):
    new_p_lines = []
    for p_line in p_lines:
        new_p_lines.append(p_line.scale(scale).translate(x_off, y_off))
    return new_p_lines    

In [778]:
sa_center_multi = [make_radical_multi((0.1, 0.9, 0.5, 0.5), (0.1, 0.9, 0.5, 0.5), (2, 8, 4, 2), randint(1, 4)) for i in range(8)]
# sa_left_radicals_multi = [make_radical_multi((0, 0.8, 0.4, 0.5), (0.2, 1, 0.6, 0.5), (2, 8, 4, 2), randint(1, 3)) for i in range(16)]
# sa_right_radicals_multi = [make_radical_multi((0.3, 1, 0.65, 0.5), (0, 1, 0.7, 0.5), (2, 8, 4, 2), randint(1, 3)) for i in range(16)]
# sa_top_radicals_multi = [make_radical_multi((0, 1, 0.5, 0.5), (0, 0.7, 0.2, 0.5), (2, 8, 4, 2), randint(1, 3)) for i in range(16)]
# sa_bottom_radicals_multi = [make_radical_multi((0, 1, 0.5, 0.5), (0.3, 1, 0.8, 0.5), (2, 8, 4, 2), randint(1, 3)) for i in range(16)]
sa_left_radicals_multi = [scale_shift_radical_multi(sa, 0.9, -0.1, 0) for sa in sa_center_multi]
sa_right_radicals_multi = [scale_shift_radical_multi(sa, 0.9, 0.1, 0) for sa in sa_center_multi]
sa_top_radicals_multi = [scale_shift_radical_multi(sa, 0.9, 0, -0.1) for sa in sa_center_multi]
sa_bottom_radicals_multi = [scale_shift_radical_multi(sa, 0.9, 0, 0.1) for sa in sa_center_multi]

In [794]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
print(thicknesses + thicknesses)
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        radical_multi_strokes = sa_center_multi[choice(len(sa_center_multi)-1)]
        for stroke in radical_multi_strokes:
            radical_pline = stroke.scale(grid_size * normal(0.67, 0.15)).translate(3 + i * grid_size, 3 + j * grid_size)
            tightness = normal(-0.5, 0.5)
#             print(radical_pline.augment().catmull_spline(tightness).beziers)
            poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses, tightness=tightness)
            poly = figure.polygon(poly)
            page.place(poly)
        
show(page)

[0.4        0.52691173 0.65369568 0.78022417 0.90636981 1.03200558
 1.15700498 1.28124213 1.40459195 1.52693023 1.64813378 1.76808057
 1.88664982 2.00372214 2.11917965 2.23290609 2.34478694 2.45470957
 2.56256327 2.66823946 2.77163172 2.87263594 2.97115044 3.067076
 3.16031605 3.25077669 3.33836683 3.4229983  3.50458586 3.58304736
 3.65830381 3.73027942 3.79890172 3.86410162 3.92581345 3.9839751
 4.03852798 4.08941718 4.13659144 4.18000327 4.21960897 4.25536863
 4.28724627 4.31520978 4.33923101 4.35928577 4.37535386 4.3874191
 4.39546936 4.39949651 4.39949651 4.39546936 4.3874191  4.37535386
 4.35928577 4.33923101 4.31520978 4.28724627 4.25536863 4.21960897
 4.18000327 4.13659144 4.08941718 4.03852798 3.9839751  3.92581345
 3.86410162 3.79890172 3.73027942 3.65830381 3.58304736 3.50458586
 3.4229983  3.33836683 3.25077669 3.16031605 3.067076   2.97115044
 2.87263594 2.77163172 2.66823946 2.56256327 2.45470957 2.34478694
 2.23290609 2.11917965 2.00372214 1.88664982 1.76808057 1.64813378

The try to connect the strokes by combining them as one polyline, and map the thickness correspondingly.

In [ ]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
print(thicknesses + thicknesses)
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        radical_multi_strokes = sa_center_multi[choice(len(sa_center_multi)-1)]
        for stroke in radical_multi_strokes:
            radical_pline = stroke.scale(grid_size * normal(0.67, 0.15)).translate(3 + i * grid_size, 3 + j * grid_size)
            tightness = normal(-0.5, 0.5)
#             print(radical_pline.augment().catmull_spline(tightness).beziers)
# len(thickness = samples_per * number of beziers * number of strokes)
            poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses, tightness=tightness)
            poly = figure.polygon(poly)
            page.place(poly)
        
show(page)

use combinations to make chars:
1. one radical: sa_center
2. combinations of two radicals: left + sa_right, sa_left + right, top + sa_bottom, sa_top + bottom
3. combinations of three radicals: top + left + sa_right, top + sa_left + right, left + sa_right + bottom, sa_left + right + bottom

In [782]:
def make_char_1():
    return choice(sa_center_multi)

def make_char_2():
    comb = randint(0, 4)
    switcher = {
                0: [choice(left_radicals)] + choice(sa_right_radicals_multi),
                1: choice(sa_left_radicals_multi) + [choice(right_radicals)],
                2: [choice(top_radicals)] + choice(sa_bottom_radicals_multi),
                3: choice(sa_top_radicals_multi) + [choice(bottom_radicals)]
                }
    return switcher.get(comb)

def make_char_3():
    comb = randint(0, 4)
    switcher = {
                0: [choice(top_radicals)] + [choice(left_radicals)] + choice(sa_right_radicals_multi),
                1: [choice(top_radicals)] + choice(sa_left_radicals_multi) + [choice(right_radicals)],
                2: [choice(left_radicals)] + choice(sa_right_radicals_multi) + [choice(bottom_radicals)],
                3: choice(sa_left_radicals_multi) + [choice(right_radicals)] + [choice(bottom_radicals)]
                }
    return switcher.get(comb)

In [795]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        char_multi_strokes = make_char_1()
#         print(char_multi_strokes)
        for stroke in char_multi_strokes:
            radical_pline = stroke.scale(grid_size * normal(0.67, 0.1)).translate(3 + i * grid_size, 3 + j * grid_size)
            poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses, tightness=normal(-0.5, 0.5))
            poly = figure.polygon(poly)
            page.place(poly)
        
show(page)

In [783]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        char_multi_strokes = make_char_2()
#         print(char_multi_strokes)
        for stroke in char_multi_strokes:
            radical_pline = stroke.scale(grid_size * normal(0.67, 0.1)).translate(3 + i * grid_size, 3 + j * grid_size)
            poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses, tightness=normal(-0.5, 0.5))
            poly = figure.polygon(poly)
            page.place(poly)
        
show(page)

In [796]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
size = 300
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 255))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        char_multi_strokes = make_char_3()
#         print(char_multi_strokes)
        for stroke in char_multi_strokes:
            radical_pline = stroke.scale(grid_size * normal(0.67, 0.1)).translate(3 + i * grid_size, 3 + j * grid_size)
            poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses, tightness=normal(-0.5, 0.5))
            poly = figure.polygon(poly)
            page.place(poly)
        
show(page)

Then putting them together

In [815]:
thicknesses = (np.sin(np.linspace(0, np.pi, 100))+0.1) * 2
size = 250
d = document(size, size, 'mm')
page = d.addpage()
figure = shape().nostroke().fill(rgba(0, 0, 0, 200))
grid_n = 8
grid_size = size / grid_n
for i in range(grid_n):
    for j in range(grid_n):
        idx = randint(1, 3)
        if idx == 0:
            char_multi_strokes = make_char_1()
        elif idx == 1:
            char_multi_strokes = make_char_2()
        else:
            char_multi_strokes = make_char_3()
#         print(char_multi_strokes)
        for stroke in char_multi_strokes:
            radical_pline = stroke.scale(grid_size * normal(0.67, 0.1)).translate(5 + i * grid_size * 1.2, 3 + j * grid_size * 0.6)
            poly = radical_pline.augment().fancy_curve(samples_per=54, thicknesses=thicknesses, tightness=normal(-0.5, 0.5))
            poly = figure.polygon(poly)
            page.place(poly)
        
show(page)

1. connect vertical characters
2. add randomness to the pts
3. make connections between radicals

Question: how to "untangle" the spline? / how to get away from the "carmull" style?

In [11]:
char_1s = [make_char_1() for i in range(26)]
char_2s = [make_char_1() for i in range(26)]
char_3s = [make_char_1() for i in range(26)]

In [ ]:
def combine_stroke(stroke_1, stroke_2):
    combined_stroke = stroke_1 + stroke_2
    return combined_stroke

def make_word_vertical(chars, row_height):
    all_strokes = []
    stroke_connection_pts = []
    stroke_count = 0
    
    for i in len(chars):
        for stroke in chars[i]:
            all_strokes += stroke.translate(0, i*1.5)
            stroke_count += 1
        stroke_connection_pts.append(stroke_count)
        
    final_word_strokes = []
    
    for pt in stroke_connection_pts:
        combined_stroke = combine_stroke(all_strokes[pt], all_strokes[pt+1])
        all_strokes.pop(pt)
        all_strokes.pop(pt)
        
        
    
    return 


In [797]:
d = document(150, 150, 'mm')
page = d.addpage()
line_fig = shape().stroke(rgba(128, 0, 128, 255)).nofill()
curve_fig = shape().stroke(rgba(0, 128, 128, 255)).nofill()
for col in range(6):
    line = choice(chars)
    for row in range(1, 10):
        # scale(normal(...)) adds a bit of size variation to the glyphs
        line += choice(chars).scale(normal(1, 0.25)).translate(0, row*1.5)
    # translate the row to the right place on the screen and make it bigger
    line = line.translate(1+col*3, 1).scale(9)
    smooth = line.smooth_path()
#     page.place(line_fig.polyline(line)) # uncomment to see original polylines
    page.place(curve_fig.path(smooth))
show(page)